In [1]:
import pennylane as qml
import random
import os
import pandas as pd
import torch
import numpy as np
import matplotlib.pyplot as plt
os.chdir('../')

In [2]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [3]:
print(device)

cuda


# Quantum Circuit

In [4]:
date = '20211122_120334'

resume_iters = 30

test_sample_size = 100000

layer = 2

qubits = 8

In [5]:
dev = qml.device('default.qubit', wires=qubits)
@qml.qnode(dev, interface='torch', diff_method='backprop')
def gen_circuit(w):
    # random noise as generator input
    z1 = random.uniform(-1, 1)
    z2 = random.uniform(-1, 1)
    
    # construct generator circuit for both atom vector and node matrix
    for i in range(qubits):
        qml.RY(np.arcsin(z1), wires=i)
        qml.RZ(np.arcsin(z2), wires=i)
    for l in range(layer):
        for i in range(qubits):
            qml.RY(w[i], wires=i)
        for i in range(qubits-1):
            qml.CNOT(wires=[i, i+1])
            qml.RZ(w[i+qubits], wires=i+1)
            qml.CNOT(wires=[i, i+1])
    return [qml.expval(qml.PauliZ(i)) for i in range(qubits)]

In [6]:
model_dir_path = r'/home/ken/projects/QuantumGAN-PyTorch/results/quantum-GAN/'+date+'/train/model_dir'

weights_pth = os.path.join(model_dir_path, 'molgan_red_weights.csv')

weights = pd.read_csv(weights_pth, header=None).iloc[resume_iters-1, 1:].values

gen_weights = torch.tensor(list(weights), requires_grad=True)

In [7]:
sample_list = [gen_circuit(gen_weights) for i in range(test_sample_size)]

In [8]:
sample_list[0]

tensor([ 0.5648,  0.1830, -0.4142, -0.0337,  0.7679,  0.7447,  0.9254,  0.7108],
       dtype=torch.float64, grad_fn=<CatBackward>)

# Data

In [9]:
from data.sparse_molecular_dataset import SparseMolecularDataset

In [10]:
mol_data_dir = 'data/gdb9_9nodes.sparsedataset'

In [11]:
data = SparseMolecularDataset()

data.load(mol_data_dir)

# Generator

In [12]:
from models.models import Generator, Discriminator

In [13]:
complexity = 'mr'

z_dim = qubits

dropout = 0.0

In [14]:
if complexity == 'nr':
    g_conv_dim = [128, 256, 512]
elif complexity == 'mr':
    g_conv_dim = [128]
elif complexity == 'hr':
    g_conv_dim = [16]
else:
    raise ValueError("Please enter an valid model complexity from 'mr', 'hr' or 'nr'!")

In [15]:
G = Generator(g_conv_dim, z_dim, data.vertexes, data.bond_num_types, data.atom_num_types, dropout)

In [16]:
G.to(device)

Generator(
  (activation_f): Tanh()
  (multi_dense_layers): MultiDenseLayers(
    (activation): Tanh()
    (linear_layers): Sequential(
      (0): Linear(in_features=8, out_features=128, bias=True)
      (1): Tanh()
      (2): Dropout(p=0.0, inplace=False)
    )
  )
  (edges_layer): Linear(in_features=128, out_features=405, bias=True)
  (nodes_layer): Linear(in_features=128, out_features=45, bias=True)
  (dropout): Dropout(p=0.0, inplace=False)
)

In [17]:
G_path = os.path.join(model_dir_path, '{}-G.ckpt'.format(resume_iters))

In [18]:
G.load_state_dict(torch.load(G_path, map_location=lambda storage, loc: storage))

<All keys matched successfully>

# Generating Molecules

In [19]:
import torch.nn.functional as F

In [20]:
z = torch.stack(tuple(sample_list)).to(device).float()

In [21]:
post_method = 'softmax'

In [22]:
edges_logits, nodes_logits = G(z)

In [23]:
def postprocess(inputs, method, temperature=1.0):
    def listify(x):
        return x if type(x) == list or type(x) == tuple else [x]
    def delistify(x):
        return x if len(x) > 1 else x[0]
    if method == 'soft_gumbel':
        softmax = [F.gumbel_softmax(e_logits.contiguous().view(-1, e_logits.size(-1))/temperature, hard=False).view(e_logits.size()) for e_logits in listify(inputs)]
    elif method == 'hard_gumbel':
        softmax = [F.gumbel_softmax(e_logits.contiguous().view(-1, e_logits.size(-1))/temperature, hard=True).view(e_logits.size()) for e_logits in listify(inputs)]
    else:
        softmax = [F.softmax(e_logits/temperature, -1) for e_logits in listify(inputs)]
    return [delistify(e) for e in (softmax)]

In [24]:
(edges_hat, nodes_hat) = postprocess((edges_logits, nodes_logits), post_method)   

In [25]:
def get_gen_mols(data, n_hat, e_hat, method):
    (edges_hard, nodes_hard) = postprocess((e_hat, n_hat), method)
    edges_hard, nodes_hard = torch.max(edges_hard, -1)[1], torch.max(nodes_hard, -1)[1]
    mols = [data.matrices2mol(n_.data.cpu().numpy(), e_.data.cpu().numpy(), strict=True) for e_, n_ in zip(edges_hard, nodes_hard)]
    return mols

In [26]:
mols = get_gen_mols(data, nodes_logits, edges_logits, post_method)

RDKit ERROR: [14:00:47] non-ring atom 1 marked aromatic
[14:00:47] non-ring atom 1 marked aromatic
RDKit ERROR: [14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:00:47] Explicit valence for atom # 8 C, 5, is greater than permitted
[14:00:47] Explicit valence for atom # 8 C, 5, is greater than permitted
RDKit ERROR: [14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:00:47] Explicit valence for atom # 7 O, 4, is greater than permitted
[14:00:47] Explicit valence for atom # 7 O, 4, is greater than permitted
RDKit ERROR: [14:00:47] non-ring atom 0 marked aromatic
[14:00:47] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:47] Can't kekulize mol.  Unkekulized atoms: 1 3 4 6 8
RDKit ERROR: 
[14:00:47] Can't kekulize mol.  Unkekulized atoms: 1 3 4 6 8

RDKit ERROR: [14

RDKit ERROR: [14:00:47] non-ring atom 0 marked aromatic
[14:00:47] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:47] non-ring atom 0 marked aromatic
[14:00:47] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:47] Can't kekulize mol.  Unkekulized atoms: 1 3 4 6 8
RDKit ERROR: 
RDKit ERROR: [14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:47] Can't kekulize mol.  Unkekulized atoms: 1 3 4 6 8

[14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:00:47] Explicit valence for atom # 0 C, 5, is greater than permitted
[14:00:47] Explicit valence for atom # 0 C, 5, is greater than permitted
RDKit ERROR: [14:00:47] non-ring atom 0 marked aromatic
[14:00:47] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:47] Can't kekulize mol.  Unkekulized atoms: 4 6 8
[14:00:47] Can't kekulize mol.  Unkekulized atoms: 4 6 8

RDKit ERROR: 
RDKit ERROR: [14:00:47] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:

RDKit ERROR: [14:00:48] non-ring atom 0 marked aromatic
[14:00:48] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:48] Explicit valence for atom # 7 O, 4, is greater than permitted
[14:00:48] Explicit valence for atom # 7 O, 4, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:48] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:00:48] non-ring atom 1 marked aromatic
[14:00:48] non-ring atom 1 marked aromatic
RDKit ERROR: [14:00:48] Explicit valence for atom # 4 N, 4, is greater than permitted
[14:00:48] Explicit valence for atom # 4 N, 4, is greater than permitted
RDKit ERROR: [14:00:48] non-ring atom 0 marked aromatic
[14:00:48] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:48] Explicit valence for atom # 5 C, 5, is greater than permitted
[14:00:48] Explicit valence for atom # 5 C, 5, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 2 O, 3, is grea

RDKit ERROR: [14:00:48] Explicit valence for atom # 6 C, 5, is greater than permitted
[14:00:48] Explicit valence for atom # 6 C, 5, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:48] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:00:48] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:00:48] non-ring atom 0 marked aromatic
[14:00:48] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:48] Explicit valence for atom # 7 O, 4, is greater than permitted
[14:00:48] Explicit valence for atom # 7 O, 4, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 0 C, 5, is greater than permitted
[14:00:48] Explicit valence for atom # 0 C, 5, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 8 C, 5, is greater than permitted
[14:00:48] Explicit 

RDKit ERROR: [14:00:48] non-ring atom 0 marked aromatic
[14:00:48] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:48] Explicit valence for atom # 5 O, 4, is greater than permitted
[14:00:48] Explicit valence for atom # 5 O, 4, is greater than permitted
RDKit ERROR: [14:00:48] non-ring atom 0 marked aromatic
[14:00:48] non-ring atom 0 marked aromatic
RDKit ERROR: [14:00:48] Explicit valence for atom # 5 C, 5, is greater than permitted
[14:00:48] Explicit valence for atom # 5 C, 5, is greater than permitted
RDKit ERROR: [14:00:48] Explicit valence for atom # 3 O, 3, is greater than permitted
[14:00:48] Explicit valence for atom # 3 O, 3, is greater than permitted
RDKit ERROR: [14:00:48] Can't kekulize mol.  Unkekulized atoms: 0 1 8
RDKit ERROR: 
[14:00:48] Can't kekulize mol.  Unkekulized atoms: 0 1 8

RDKit ERROR: [14:00:48] non-ring atom 3 marked aromatic
[14:00:48] non-ring atom 3 marked aromatic
RDKit ERROR: [14:00:48] non-ring atom 1 marked aromatic
[14:00:48] non-ring atom 1 m

...

[14:01:18] non-ring atom 0 marked aromatic
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] non-ring atom 0 marked aromatic
RDKit ERROR: [14:01:18] Explicit valence for atom # 7 C, 5, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] non-ring atom 0 marked aromatic
[14:01:18] Explicit valence for atom # 7 C, 5, is greater than permitted
RDKit ERROR: [14:01:18] non-ring atom 1 marked aromatic
[14:01:18] non-ring atom 1 marked aromatic
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 8 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 8 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 8 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom 

RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 8 C, 5, is greater than permitted
[14:01:18] Explicit valence for atom # 8 C, 5, is greater than permitted
RDKit ERROR: [14:01:18] Can't kekulize mol.  Unkekulized atoms: 1 3 4 6 8
RDKit ERROR: 
[14:01:18] Can't kekulize mol.  Unkekulized atoms: 1 3 4 6 8

RDKit ERROR: [14:01:18] Explicit valence for atom # 6 C, 5, is greater than permitted
[14:01:18] Explicit valence for atom # 6 C, 5, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 0 N

RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] non-ring atom 0 marked aromatic
[14:01:18] non-ring atom 0 marked aromatic
RDKit ERROR: [14:01:18] Can't kekulize mol.  Unkekulized atoms: 0 1 8
[14:01:18] Can't kekulize mol.  Unkekulized atoms: 0 1 8

RDKit ERROR: 
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 8 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 8 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom 

RDKit ERROR: 
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 6 C, 5, is greater than permitted
[14:01:18] Explicit valence for atom # 6 C, 5, is greater than permitted
RDKit ERROR: [14:01:18] non-ring atom 0 marked aromatic
[14:01:18] non-ring atom 0 marked aromatic
RDKit ERROR: [14:01:18] non-ring atom 1 marked aromatic
[14:01:18] non-ring atom 1 marked aromatic
RDKit ERROR: [14:01:18] Explicit valence for atom # 5 C, 5, is greater than permitted
[14:01:18] Explicit valence for atom # 5 C, 5, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:18] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:18] Explicit valence for atom # 4 N, 4, is greater than permitted
[14:01:18] Explicit valence for atom # 4 N, 4, is greater than per

RDKit ERROR: [14:01:19] Explicit valence for atom # 6 C, 5, is greater than permitted
[14:01:19] Explicit valence for atom # 6 C, 5, is greater than permitted
RDKit ERROR: [14:01:19] Can't kekulize mol.  Unkekulized atoms: 0 1 8
RDKit ERROR: 
[14:01:19] Can't kekulize mol.  Unkekulized atoms: 0 1 8

RDKit ERROR: [14:01:19] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:19] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:19] non-ring atom 1 marked aromatic
[14:01:19] non-ring atom 1 marked aromatic
RDKit ERROR: [14:01:19] Explicit valence for atom # 0 O, 3, is greater than permitted
[14:01:19] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [14:01:19] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:19] Explicit valence for atom # 2 O, 3, is greater than permitted
RDKit ERROR: [14:01:19] Explicit valence for atom # 2 O, 3, is greater than permitted
[14:01:19] Explicit valence for atom 

# Scores

In [27]:
from utils.utils import *

In [ ]:
m0, m1 = all_scores(mols, data, norm=True)

In [ ]:
from collections import defaultdict

scores = defaultdict(list)

for k, v in m1.items():
    scores[k].append(v)
for k, v in m0.items():
    scores[k].append(np.array(v)[np.nonzero(v)].mean())

In [ ]:
scores

In [ ]:
v = MolecularMetrics.valid_filter(mols)

In [ ]:
s = set(map(lambda x: Chem.MolToSmiles(x), v))

In [ ]:
print(len(s))

In [ ]:
from rdkit.Chem import Draw

unique_mols = list(map(lambda x: Chem.MolFromSmiles(x), s))

In [ ]:
img=Draw.MolsToGridImage(unique_mols,molsPerRow=8,subImgSize=(200,200), maxMols=200)    

In [ ]:
img

In [ ]:
df = pd.DataFrame({'SMIELS': data} for data in s)

In [ ]:
df.to_csv('quantum-'+str(resume_iters)+'.csv', index=False)